In [1]:
import os
import sys
import pandas as pd
import matplotlib.pyplot as plt
import re

module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)

#import fasttext
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split
import neattext as nt
import neattext.functions as nfx
from sklearn import tree
import matplotlib
from sklearn.ensemble import RandomForestClassifier 
from sklearn.datasets import make_classification
from nltk.tokenize import sent_tokenize, word_tokenize
import warnings
from sklearn.metrics import accuracy_score
import numpy as np
import json
import requests
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
import functools
 
warnings.filterwarnings(action='ignore')

from code_utils.utils import preprocess

In [2]:
df_ipcc=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\data_ipcc.jsonl', lines= True).dropna(subset=['year'])

In [3]:
df_ipcc=df_ipcc.dropna(subset=['year'])

In [4]:
df_not_ipcc=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\data_not_ipcc.jsonl', lines= True)

In [5]:
df_ipcc=df_ipcc[['doi', 'title','topics','locations_names','locations_ids']]

In [6]:
df_not_ipcc=df_not_ipcc[['doi', 'title','topics','locations_names','locations_ids']]

In [7]:
df_ipcc=df_ipcc.dropna(subset=['doi', 'title','topics','locations_names','locations_ids']).drop_duplicates(subset=['doi'])

In [8]:
df_not_ipcc=df_not_ipcc.dropna(subset=['doi', 'title','topics','locations_names','locations_ids'])

In [9]:
print(len(df_ipcc),len(df_not_ipcc))

48219 47737


In [10]:
df_ipcc['label']=1
df_not_ipcc['label']=0

In [11]:
df_all=pd.concat([df_ipcc,df_not_ipcc]).reset_index()
del df_all['index']

In [12]:
df_all.to_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\data_model.json')

make vectors with embedding method

In [ ]:
#pip install -U sentence-transformers

In [2]:
from sentence_transformers import SentenceTransformer, util

sentence_transformer_model = SentenceTransformer("thenlper/gte-large")

DEBUG:tensorflow:Falling back to TensorFlow client; we recommended you install the Cloud TPU client directly with pip install cloud-tpu-client.
DEBUG:h5py._conv:Creating converter from 7 to 5
DEBUG:h5py._conv:Creating converter from 5 to 7
DEBUG:h5py._conv:Creating converter from 7 to 5
DEBUG:h5py._conv:Creating converter from 5 to 7
INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: cpu
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: thenlper/gte-large
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): huggingface.co:443
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "HEAD /thenlper/gte-large/resolve/main/modules.json HTTP/1.1" 200 0
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "HEAD /thenlper/gte-large/resolve/main/config_sentence_transformers.json HTTP/1.1" 404 0
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "HEAD /thenlper/gte-large/resolve/main/README.md HTTP/1.1" 200 0
DEBUG:urllib

In [3]:
def get_embeddings(text):
    tokvecs = sentence_transformer_model.encode(text, normalize_embeddings=True)
    return [float(e) for e in tokvecs]

In [4]:
df_all=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\data_model.json')

In [5]:
ipcc_vectors=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\ipcc_vectors.json')

In [6]:
df_all=pd.merge(df_all, ipcc_vectors, how='left', on='doi')

In [ ]:
df_all.loc[pd.isna(df_all.title_vect),'title_vect']=df_all.loc[pd.isna(df_all.title_vect),'title'].apply(lambda x: get_embeddings(nfx.remove_stopwords(x.replace('{','').replace('}',''))))

In [ ]:
df_all[['doi','title_vect']].to_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\title.json')

In [25]:
df_all['locations_names_vect']=df_all['locations_names'].apply(lambda x: get_embeddings(nfx.remove_stopwords(x.lower().replace('journal','').replace('letters',''))))

Batches: 100%|██████████| 1/1 [00:01<00:00,  1.05s/it]


In [26]:
df_all[['doi','locations_names_vect']].to_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\locations_names.json')

In [7]:
df_all.loc[pd.isna(df_all.locations_ids_vect),'locations_ids_vect']=df_all.loc[pd.isna(df_all.locations_ids_vect),'locations_ids'].apply(lambda x: get_embeddings(nfx.remove_stopwords(x)))

Batches: 100%|██████████| 1/1 [00:00<00:00,  1.16it/s]


In [8]:
df_all[['doi','locations_ids_vect']].to_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\locations_ids.json')

In [ ]:
df_all.loc[pd.isna(df_all.topics_vect),'topics_vect']=df_all.loc[pd.isna(df_all.topics_vect),'topics'].apply(lambda x: get_embeddings(' '.join(x)) if isinstance(x,list) else None)

In [ ]:
df_all[['doi','topics_vect']].to_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\topics.json')

In [ ]:
df_all.to_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\data_model_vect.json')

read the embeddings

In [ ]:
df_all=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\data_model_vect.json')
del df_all['title_vect']

In [ ]:
title=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\title.json')

In [ ]:
topics=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\topics.json')

In [ ]:
locations_ids=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\locations_ids.json')

In [ ]:
print(len(title),len(topics),len(locations_ids))

In [ ]:
ipcc_vectors=pd.read_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\ipcc_vectors.json')

In [ ]:
df_ipcc_all=pd.merge(df_all[['doi','label']],pd.concat([title,topics['topics_vect'],locations_ids['locations_ids_vect']], axis=1), on='doi', how='right')

In [ ]:
df=df_ipcc_all[df_ipcc_all.label==1]
del df['label']
df.to_json(module_path+f'\\IPCC_bibliography\\AR6\\structured_data\\data_model_ipcc\\ipcc_vectors.json')

In [ ]:
df_all.dropna().label.value_counts()

In [ ]:
df_all[['title','topics','label']][47730:47750]

In [ ]:
title

In [ ]:
topics

In [ ]:
locations_ids

split the data into training and test datasets

In [ ]:
X=pd.concat([pd.DataFrame(df_all['title_vect']),pd.DataFrame(mlb.fit_transform(df_all['topics_name']), columns=mlb.classes_)], axis=1).dropna()
y=df_all['label']

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

random forest

In [ ]:
forest = RandomForestClassifier(n_estimators = 100)

print("Fitting a random forest to labeled training data...")
forest = forest.fit(trainDataVecs, train_reviews['Class'])

In [ ]:
modele_rf  = RandomForestClassifier(n_estimators=100, criterion='gini')

In [ ]:
modele_rf.fit(X_train, y_train)

In [ ]:
predictions = modele_rf.predict(X_test)
accuracy_score(y_test, predictions)

In [ ]:
pd.DataFrame(modele_rf.feature_importances_,
              index = X_train.columns, 
              columns = ["importance"]).sort_values(
     "importance", 
     ascending = False)

In [ ]:
test_data = X_test.copy()
test_data['true_label'] = y_test

In [ ]:
X_test

In [ ]:
y_test

In [ ]:
sampled_data = test_data.sample(n=20, random_state=42)

X_sample = sampled_data.drop(columns=['true_label'])
y_sample = sampled_data['true_label']

In [ ]:
sampled_data['predicted_label'] = modele_rf.predict(X_sample)

In [ ]:
sampled_data.loc[sampled_data['predicted_label']==1,['true_label','predicted_label']].head()

In [ ]:
sampled_data['Waterborne Disease Outbreaks and Pathogen Transport']

In [ ]:
df_all.iloc[60187,:].topics_name

decision tree

In [ ]:
#3
tree.plot_tree(dtree, feature_names=list(X.columns))

In [ ]:
#10
tree.plot_tree(dtree, feature_names=list(X.columns))

In [ ]:
#50
tree.plot_tree(dtree, feature_names=list(X.columns))